In [3]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import yaml
import pandas as pd
import numpy as np
from functools import partial
import multiprocessing
import tensorflow as tf
from pathlib import Path
from time import strftime
from shutil import rmtree
import matplotlib.pyplot as plt
from tqdm import tqdm
import matplotlib
matplotlib.use("TKAgg", force=True)
%matplotlib inline
#pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [4]:
from rtapipe.lib.utils.misc import dotdict
from rtapipe.lib.dataset.data_manager import DataManager
from rtapipe.lib.datasource.Photometry3 import OnlinePhotometry, SimulationParams
from rtapipe.lib.plotting.plotting import plot_sequences
from rtapipe.lib.models.anomaly_detector_builder import AnomalyDetectorBuilder
from rtapipe.lib.evaluation.pval import get_pval_table, get_threshold_for_sigma
from rtapipe.lib.standardanalysis.li_ma import LiMa
from rtapipe.lib.evaluation.pval import get_pval_table, get_threshold_for_sigma, get_sigma_from_pvalue, get_sigma_for_ts_array, get_sigma_from_ts

# Loading the models

In [5]:
def load_model(model_id):
    with open("./trained_models.yaml", "r") as f:
        try:
            configs = yaml.safe_load(f)
        except yaml.YAMLError as exc:
            print(exc)
    model_config = dotdict([c for c in configs["models"] if c["id"] == model_id].pop())
    model_config.ad = AnomalyDetectorBuilder.getAnomalyDetector(name=model_config.name, timesteps=model_config.timesteps, nfeatures=model_config.nfeatures, load_model="True", training_epoch_dir=model_config.path, training=False)
    model_config.pvalue_table = get_pval_table(model_config.pval_path)
    return model_config

In [6]:
model_config_cnn = load_model(0)
model_config_cnn

AnomalyDetector_cnn_l2_u32 - input shape: (5,3)


{'id': 0,
 'patience': 5,
 'integrationtime': 5,
 'timesteps': 5,
 'nfeatures': 3,
 'scaler': 'minmax',
 'name': 'AnomalyDetector_cnn_l2_u32',
 'path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_cnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/epochs/epoch_19',
 'epoch': 19,
 'pval_path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_cnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/epochs/epoch_19/pvalues/pval_20221118-113940/pvalue_bins_100_0.numpy.txt',
 'scaler_path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_cnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/fitted_scaler.pickle',
 'ad': <rtapipe.lib.models.anomaly_detector_cnn.AnomalyDetector_cnn_l2_u32 at 0x2b6f4cc1ef10>,
 'pvalue_table':     threshold  threshold_err        pvalue    pvalue_err  sigma
 0    0.003171       0.000

In [7]:
with open("./trained_models.yaml", "r") as f:
    try:
        configs = yaml.safe_load(f)
    except yaml.YAMLError as exc:
        print(exc)
configs = [dotdict(c) for c in configs["models"]]

In [8]:
model_config_rnn = load_model(1)
model_config_rnn

AnomalyDetector_rnn_l2_u32 - input shape: (5,3)


{'id': 1,
 'patience': 5,
 'integrationtime': 5,
 'timesteps': 5,
 'nfeatures': 3,
 'scaler': 'minmax',
 'name': 'AnomalyDetector_rnn_l2_u32',
 'path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_rnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/epochs/epoch_10',
 'epoch': 10,
 'pval_path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_rnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/epochs/epoch_10/pvalues/pval_20221121-132236/pvalue_bins_100_0.numpy.txt',
 'scaler_path': '/data01/homes/baroncelli/phd/rtapipe/notebooks/run_20221116-101109_mr_patience_5/model_AnomalyDetector_rnn_l2_u32_dataset_train_itime_5_a_tsl_5_nbins_3_tsl_3600/fitted_scaler.pickle',
 'ad': <rtapipe.lib.models.anomaly_detector_rnn.AnomalyDetector_rnn_l2_u32 at 0x2b6f5fedd6d0>,
 'pvalue_table':     threshold  threshold_err        pvalue    pvalue_err  sigma
 0    0.000227       0.000

# Loading the test dataset

In [9]:
output_dir = "./logs/test_models_dataset_itime_5_c_out"

In [10]:
features_names = ["EB_0.04-0.117","EB_2-0.117-0.342","EB_0.342-1"]

In [11]:
data_manager = DataManager(output_dir)

In [12]:
dataset_id="test_itime_5_c_tsl_5_nbins_3"

In [13]:
dataset_folder = "/data01/homes/baroncelli/phd/rtapipe/scripts/ml/dataset_generation/test/itime_5_c/fits_data"
fits_files = DataManager.load_fits_data(dataset_folder, limit=210)
test_set_size = len(fits_files)

Loaded 209 files


In [14]:
sim_params = SimulationParams(runid=None, onset=250, emin=0.04, emax=1, tmin=0, tobs=500, offset=0.5, irf="North_z40_5h_LST", roi=2.5, caldb="prod5-v0.1", simtype="grb")
multiple_templates = True
add_target_region = True
integration_time = 5
number_of_energy_bins = 3
tsl = 100
threads = 30
normalize = True
#data_manager.transform_to_timeseries(fits_files, sim_params, add_target_region, integration_time=integration_time, number_of_energy_bins=number_of_energy_bins, tsl=tsl, normalize=normalize, threads=threads, multiple_templates=multiple_templates)
data_manager.load_saved_data(5, 100)

Loading cached data from run0002_ID000044_it_5_tsl_100.npy
Loading cached data from run0011_ID000139_it_5_tsl_100.npy
Loading cached data from run0016_ID000340_it_5_tsl_100.npy
Loading cached data from run0017_ID000132_it_5_tsl_100.npy
Loading cached data from run0017_ID000261_it_5_tsl_100.npy
Loading cached data from run0019_ID000070_it_5_tsl_100.npy
Loading cached data from run0019_ID000268_it_5_tsl_100.npy
Loading cached data from run0025_ID000471_it_5_tsl_100.npy
Loading cached data from run0026_ID000127_it_5_tsl_100.npy
Loading cached data from run0029_ID000397_it_5_tsl_100.npy
Loading cached data from run0029_ID000446_it_5_tsl_100.npy
Loading cached data from run0032_ID000190_it_5_tsl_100.npy
Loading cached data from run0038_ID000228_it_5_tsl_100.npy
Loading cached data from run0043_ID000231_it_5_tsl_100.npy
Loading cached data from run0043_ID000324_it_5_tsl_100.npy
Loading cached data from run0043_ID000460_it_5_tsl_100.npy
Loading cached data from run0046_ID000029_it_5_tsl_100.n

In [15]:
assert len(data_manager.data) == test_set_size-1

## Plot some samples

In [16]:
for template in list(data_manager.data.keys())[0:5]:
    data_manager.plot_timeseries(template, data_manager.data[template], 1, sim_params, output_dir, labels=features_names)

Produced: logs/test_models_dataset_itime_5_c_out/template_run0002_ID000044_trial_0_2022-12-20 15:00:47.184100.png
Saved: ./logs/test_models_dataset_itime_5_c_out/template_run0002_ID000044_trial_0_2022-12-20 15:00:47.184100.png
Produced: logs/test_models_dataset_itime_5_c_out/template_run0011_ID000139_trial_0_2022-12-20 15:00:49.462345.png
Saved: ./logs/test_models_dataset_itime_5_c_out/template_run0011_ID000139_trial_0_2022-12-20 15:00:49.462345.png
Produced: logs/test_models_dataset_itime_5_c_out/template_run0016_ID000340_trial_0_2022-12-20 15:00:52.090644.png
Saved: ./logs/test_models_dataset_itime_5_c_out/template_run0016_ID000340_trial_0_2022-12-20 15:00:52.090644.png
Produced: logs/test_models_dataset_itime_5_c_out/template_run0017_ID000132_trial_0_2022-12-20 15:00:54.338638.png
Saved: ./logs/test_models_dataset_itime_5_c_out/template_run0017_ID000132_trial_0_2022-12-20 15:00:54.338638.png
Produced: logs/test_models_dataset_itime_5_c_out/template_run0017_ID000261_trial_0_2022-12-2

# TESTING

In [17]:
data_manager.load_scaler(model_config_rnn.scaler_path) # model_config_rnn.scaler_path or model_config_cnn.scaler_path

In [18]:
test_all_x, test_all_y = data_manager.get_test_set_all_templates(verbose=False, onset=250, integration_time=integration_time, sub_window_size=5, stride=1)

[2022-12-20 15:01:14.266365] Total x shape shape: (19968, 5, 3)
[2022-12-20 15:01:14.266433] Total y shape shape: (19968,)


# RNN

## Standard metrics - 3 sigma threshold

In [19]:
model_config_rnn.pvalue_table


threshold  threshold_err        pvalue    pvalue_err  sigma
0    0.000227       0.000013  1.416930e-01  1.254772e-04  1.073
1    0.000253       0.000013  9.859137e-02  1.046671e-04  1.290
2    0.000279       0.000013  6.802256e-02  8.693953e-05  1.491
3    0.000305       0.000013  4.666059e-02  7.200554e-05  1.678
4    0.000331       0.000013  3.223601e-02  5.984963e-05  1.849
..        ...            ...           ...           ...    ...
87   0.002495       0.000013  1.111173e-07  1.111173e-07  5.180
88   0.002521       0.000013  1.111173e-07  1.111173e-07  5.180
89   0.002547       0.000013  1.111173e-07  1.111173e-07  5.180
90   0.002574       0.000013  1.111173e-07  1.111173e-07  5.180
91   0.002600       0.000013  1.111173e-07  1.111173e-07  5.180

[92 rows x 5 columns]

In [20]:
SIGMA_THRESHOLD = 3

In [21]:
sigma_threshold = get_threshold_for_sigma(model_config_rnn.pvalue_table, SIGMA_THRESHOLD)
model_config_rnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_rnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_rnn.pvalue_table, model_config_rnn.ad.threshold)} sigma")

Threshold: 0.0005921241825 corresponding to 3.0060572682 sigma


In [22]:
print(f"************** Evaluating {model_config_rnn.name} patience={model_config_rnn.patience} **************")
metrics = model_config_rnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_rnn.ad.detection_delay(test_all_y, model_config_rnn.ad.predict(test_all_x), test_set_size, model_config_rnn.timesteps))

************** Evaluating AnomalyDetector_rnn_l2_u32 patience=5 **************
Using threshold 0.0005921241825
accuracy 0.8221153846153846
precision 0.9983488441909336
recall 0.6525706436420722
f1 0.7892488430046279
roc_auc 0.8257227195297103
confusion_matrix [[9765, 11], [3541, 6651]]
false_positive_rate 0.0016511558090663465
detection_delay: 6.759615384615385


## Standard metrics - 5 sigma threshold

In [23]:
SIGMA_THRESHOLD = 5

In [24]:
sigma_threshold = get_threshold_for_sigma(model_config_rnn.pvalue_table, SIGMA_THRESHOLD)
model_config_rnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_rnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_rnn.pvalue_table, model_config_rnn.ad.threshold)} sigma")

Threshold: 0.0020782086315 corresponding to 5.0488536162 sigma


In [25]:
print(f"************** Evaluating {model_config_rnn.name} patience={model_config_rnn.patience} **************")
metrics = model_config_rnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_rnn.ad.detection_delay(test_all_y, model_config_rnn.ad.predict(test_all_x), test_set_size, model_config_rnn.timesteps))

************** Evaluating AnomalyDetector_rnn_l2_u32 patience=5 **************
Using threshold 0.0020782086315
accuracy 0.7451422275641025
precision 0.9984371947646025
recall 0.5014717425431711
f1 0.6676245836326822
roc_auc 0.7503267059688031
confusion_matrix [[9768, 8], [5081, 5111]]
false_positive_rate 0.0015628052353975385
detection_delay: 5.25


## Sigma table

In [26]:
def crop_to_5(s):
    if s > 5: 
        s = 5.00001
    return s

In [27]:
data = {}
for template in tqdm(list(data_manager.data.keys())):
    test_x, test_y = data_manager.get_test_set(template=template, onset=250, integration_time=5, sub_window_size=5, stride=1)
    model_config_rnn.ad.predict(test_x)
    data[template] = get_sigma_for_ts_array(model_config_rnn.pvalue_table, model_config_rnn.ad.get_reconstruction_errors(), verbose=False)

sigma_table_rnn = pd.DataFrame(data, index=DataManager.get_tbin_of_sequences(96, 5, 5, 1))    
sigma_table_rnn = sigma_table_rnn.applymap(crop_to_5)

100%|████████████████████████████████████████████████████████████████████████████████████████| 208/208 [00:15<00:00, 13.38it/s]


In [28]:
sigma_table_rnn

run0002_ID000044  run0011_ID000139  run0016_ID000340  \
0-25                  0.0                 0                 0   
5-30                  0.0                 0                 0   
10-35                 0.0                 0                 0   
15-40                 0.0                 0                 0   
20-45                 0.0                 0                 0   
...                   ...               ...               ...   
455-480               0.0                 0                 0   
460-485               0.0                 0                 0   
465-490               0.0                 0                 0   
470-495               0.0                 0                 0   
475-500               0.0                 0                 0   

         run0017_ID000132  run0017_ID000261  run0019_ID000070  \
0-25                    0          0.000000           0.00000   
5-30                    0          0.000000           0.00000   
10-35                   0          0.000000           0.00000   
15-40                   0          0.000000           0.00000   
20-45                   0          0.000000           0.00000   
...                   ...               ...               ...   
455-480                 0          1.911830           5.00001   
460-485                 0          2.620257           5.00001   
465-490                 0          2.294968           5.00001   
470-495                 0          3.321574           5.00001   
475-500                 0          2.816462           5.00001   

         run0019_ID000268  run0025_ID000471  run0026_ID000127  \
0-25             0.000000                 0                 0   
5-30             0.000000                 0                 0   
10-35            0.000000                 0                 0   
15-40            1.100233                 0                 0   
20-45            1.158065                 0                 0   
...                   ...               ...               ...   
455-480          5.000010                 0                 0   
460-485          5.000010                 0                 0   
465-490          5.000010                 0                 0   
470-495          5.000010                 0                 0   
475-500          5.000010                 0                 0   

         run0029_ID000397  run0029_ID000446  run0032_ID000190  \
0-25                    0                 0                 0   
5-30                    0                 0                 0   
10-35                   0                 0                 0   
15-40                   0                 0                 0   
20-45                   0                 0                 0   
...                   ...               ...               ...   
455-480                 0                 0                 0   
460-485                 0                 0                 0   
465-490                 0                 0                 0   
470-495                 0                 0                 0   
475-500                 0                 0                 0   

         run0038_ID000228  run0043_ID000231  run0043_ID000324  \
0-25             0.000000                 0                 0   
5-30             0.000000                 0                 0   
10-35            0.000000                 0                 0   
15-40            0.000000                 0                 0   
20-45            0.000000                 0                 0   
...                   ...               ...               ...   
455-480          0.000000                 0                 0   
460-485          4.561752                 0                 0   
465-490          4.360650                 0                 0   
470-495          4.762506                 0                 0   
475-500          4.550544                 0                 0   

         run0043_ID000460  run0046_ID000029  run0046_ID000300  \
0-25                    0          0.00

# CNN

## Standard metrics - 3 sigma

In [29]:
SIGMA_THRESHOLD = 3

In [30]:
sigma_threshold = get_threshold_for_sigma(model_config_cnn.pvalue_table, SIGMA_THRESHOLD)
model_config_cnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_cnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_cnn.pvalue_table, model_config_cnn.ad.threshold)} sigma")

Threshold: 0.006506945827 corresponding to 3.0286528291 sigma


In [31]:
print(f"************** Evaluating {model_config_cnn.name} patience={model_config_cnn.patience} **************")
metrics = model_config_cnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_cnn.ad.detection_delay(test_all_y, model_config_cnn.ad.predict(test_all_x), test_set_size, model_config_cnn.timesteps))

************** Evaluating AnomalyDetector_cnn_l2_u32 patience=5 **************
Using threshold 0.006506945827
accuracy 0.7659755608974359
precision 0.998374571067365
recall 0.542386185243328
f1 0.7029054612499205
roc_auc 0.770732781656034
confusion_matrix [[9767, 9], [4664, 5528]]
false_positive_rate 0.0016254289326350009
detection_delay: 6.25


## Standard metrics - 5 sigma

In [32]:
SIGMA_THRESHOLD = 5

In [33]:
sigma_threshold = get_threshold_for_sigma(model_config_cnn.pvalue_table, SIGMA_THRESHOLD)
model_config_cnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_cnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_cnn.pvalue_table, model_config_cnn.ad.threshold)} sigma")

Threshold: 0.0139048776129999 corresponding to 5.0465140766 sigma


In [34]:
print(f"************** Evaluating {model_config_cnn.name} patience={model_config_cnn.patience} **************")
metrics = model_config_cnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_cnn.ad.detection_delay(test_all_y, model_config_cnn.ad.predict(test_all_x), test_set_size, model_config_cnn.timesteps))

************** Evaluating AnomalyDetector_cnn_l2_u32 patience=5 **************
Using threshold 0.0139048776129999
accuracy 0.7098858173076923
precision 0.9986397642257991
recall 0.43220172684458397
f1 0.6033006916387044
roc_auc 0.7157939894452053
confusion_matrix [[9770, 6], [5787, 4405]]
false_positive_rate 0.0013602357742008614
detection_delay: 4.831730769230769


## Sigma table

In [ ]:
data = {}
for template in tqdm(list(data_manager.data.keys())):
    test_x, test_y = data_manager.get_test_set(template=template, onset=250, integration_time=5, sub_window_size=5, stride=1)
    model_config_cnn.ad.predict(test_x)
    data[template] = get_sigma_for_ts_array(model_config_cnn.pvalue_table, model_config_cnn.ad.get_reconstruction_errors(), verbose=False)

sigma_table_cnn = pd.DataFrame(data, index=DataManager.get_tbin_of_sequences(96, 5, 5, 1))    
sigma_table_cnn = sigma_table_cnn.applymap(crop_to_5)
sigma_table_cnn

  4%|███▉                                                                                      | 9/208 [00:00<00:14, 14.21it/s]

In [ ]:
sigma_table_cnn

# Li&Ma

In [ ]:
li_ma_data = {}
templates = list(data_manager.data.keys())
templates = []
for template in tqdm(templates):
    lima_df = LiMa.detect("binned", DataManager.get_fits_from_template(fits_files, template), temporal_bins=sigma_table_cnn.index.values, tobs=500, sigma_gt=0)
    li_ma_data[template] = lima_df["sigma"].values
lima_sigma_table = pd.DataFrame(li_ma_data, index=sigma_table_cnn.index.values)
if len(templates) > 0:
    lima_sigma_table.to_csv(Path(output_dir).joinpath("li_ma_detection_table.csv"))    

In [ ]:
lima_sigma_table = pd.read_csv(Path(output_dir).joinpath("li_ma_detection_table.csv"), index_col=0)

In [ ]:
### FIX INDEPENDENCE
for time_bin in lima_sigma_table.index:
    if int(time_bin.split("-")[1])%25 != 0:
        lima_sigma_table.loc[time_bin] = 0
lima_sigma_table

In [ ]:
lima_sigma_table = lima_sigma_table.applymap(crop_to_5)
lima_sigma_table

## Results

In [ ]:
templates_detections = dotdict({})
for templ_det in lima_sigma_table:
    templates_detections[templ_det] = dotdict({}) 
    templates_detections[templ_det]["li_ma"] = dotdict({})
    templates_detections[templ_det]["cnn"] = dotdict({})
    templates_detections[templ_det]["rnn"] = dotdict({})

In [ ]:
for templ_det in lima_sigma_table:
    detections_3s = lima_sigma_table[templ_det] >= 3
    detections_5s = lima_sigma_table[templ_det] >= 5
    templates_detections[templ_det]["li_ma"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["li_ma"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["li_ma"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["li_ma"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]

for templ_det in sigma_table_rnn:
    detections_3s = sigma_table_rnn[templ_det] >= 3
    detections_5s = sigma_table_rnn[templ_det] >= 5
    templates_detections[templ_det]["rnn"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["rnn"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["rnn"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["rnn"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]
    
for templ_det in sigma_table_cnn:
    detections_3s = sigma_table_cnn[templ_det] >= 3
    detections_5s = sigma_table_cnn[templ_det] >= 5
    templates_detections[templ_det]["cnn"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["cnn"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["cnn"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["cnn"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]    

In [ ]:
def get_dd(model, templates_detections, sigma, onset_index=45):
    first_detection_indexes = []
    for template_result in templates_detections.values():
        if len(template_result[model][f"{sigma}s_detections_indexes"]) > 0:
            #print(onset_index)
            #print(template_result[model][f"{sigma}s_detections_indexes"])
            first_detection_indexes.append(template_result[model][f"{sigma}s_detections_indexes"][0])
    return round((np.array(first_detection_indexes).mean()-onset_index)*integration_time,2)

In [ ]:
def get_detections_in_time(templates_detections, model, tmax, onset_index=45, sigma=5):
    first_detection_indexes = []
    for template_result in templates_detections.values():
        if len(template_result[model][f"{sigma}s_detections_indexes"]) > 0:
            first_detection_indexes.append(template_result[model][f"{sigma}s_detections_indexes"][0])
    detection_time = (np.array(first_detection_indexes)-onset_index)*integration_time
    dt_filterd = [dt for dt in detection_time if dt <= tmax]
    return len(dt_filterd)

print("i", "LiMa","RNN")
for i in range(0, 60, 5):
    print(i, get_detections_in_time(templates_detections, "li_ma", i), get_detections_in_time(templates_detections, "rnn", i))  

### 3 sigma detections

In [ ]:
print(f'Detected by CNN: {np.array([template_result["cnn"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("cnn",templates_detections, 3)} s')
print(f'Detected by RNN: {np.array([template_result["rnn"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("rnn",templates_detections, 3)} s')
print(f'Detected by Li&Ma: {np.array([template_result["li_ma"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("li_ma",templates_detections, 3)} s')

In [ ]:
count_rnn = 0
for template_result in templates_detections.values():
    if template_result["rnn"]["3s_detection"] and not template_result["li_ma"]["3s_detection"]:
        count_rnn += 1
print(f"Detected by RNN but not by Li&Ma: {count_rnn}")

In [ ]:
count_rnn = 0
for template_result in templates_detections.values():
    if not template_result["rnn"]["3s_detection"] and template_result["li_ma"]["3s_detection"]:
        count_rnn += 1
print(f"Detected by Li&Ma but not by RNN: {count_rnn}")

### 5 sigma detections

In [ ]:
def get_detections_in_time(templates_detections, model):
    first_detection_indexes = []
    for template_result in templates_detections.values():
        if len(template_result["li_ma"][f"5s_detections_indexes"]) > 0:
            first_detection_indexes.append(template_result["li_ma"][f"5s_detections_indexes"][0])
    detection_time = (np.array(first_detection_indexes)-45)*integration_time
    dt_filterd = [dt for dt in detection_time if dt <= 50]
    return len(dt_filterd)

print(get_detections_in_time(templates_detections, "li_ma"))

In [ ]:
print(f'Detected by CNN: {np.array([template_result["cnn"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("cnn",templates_detections, 5)} s')
print(f'Detected by RNN: {np.array([template_result["rnn"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("rnn",templates_detections, 5)} s')
print(f'Detected by Li&Ma: {np.array([template_result["li_ma"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("li_ma",templates_detections, 5)} s')

In [ ]:
count_rnn = 0
for template_result in templates_detections.values():
    if template_result["rnn"]["5s_detection"] and not template_result["li_ma"]["5s_detection"]:
        count_rnn += 1
print(f"Detected by RNN but not by Li&Ma: {count_rnn}")

In [ ]:
count_rnn = 0
for template_result in templates_detections.values():
    if not template_result["rnn"]["5s_detection"] and template_result["li_ma"]["5s_detection"]:
        count_rnn += 1
print(f"Detected by Li&Ma but not by RNN: {count_rnn}")

### Sigma plots RNN vs Li&Ma